# Goal of this notebook

Develop a training loop for finetuning ASR models using TTS loss by recreating RL training found in RL4LMs/rl4lms/envs/text_generation/training_utils.py

```bash
conda activate speller
cd /home/s1785140/rlspeller
```

# automatic reloading magic

# imports

In [373]:
import torch
from typing import List, Dict, Tuple, Any
import hyperpyyaml
from tqdm import tqdm
from torchaudio.models.decoder import ctc_decoder
from torch.nn.functional import softmax
import random
from jiwer import cer
import numpy as np
import speechbrain as sb
from IPython.display import Audio

## check if gpu available

In [374]:
# print hostname to make sure we are on correct node
import socket
print(socket.gethostname())

levi.inf.ed.ac.uk


In [375]:
torch.cuda.is_available()

True

In [376]:
import os
os.getcwd()

'/disk/nfs/ostrom/s1785140/rlspeller'

# HPARAMS

In [377]:
hparams = {
    "softdtw_temp": 0.01,
    "softdtw_bandwidth": 120,
    "dist_func": "l1",
    "sentencepiece_model_path": "/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/0_char.model",
    # 'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain_subsampling1x_nowhitespace.yaml',
    'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain_subsampling1x.yaml',
    # 'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain_subsampling2x.yaml',
    # 'speechbrain_hparams_file': '/home/s1785140/rlspeller/infer_speechbrain.yaml', # 4x subsampling
    'sample_rate': 16000,
}

# TOKENIZER

In [378]:
# load pretrained tokenizer used to tokenizer ASR training inputs 
import sentencepiece as spm 
spm_path = hparams["sentencepiece_model_path"]
sp = spm.SentencePieceProcessor()
sp.load(spm_path)
print(sp.vocab_size())

28


In [379]:
# test tokenizer
s = "hello world my name is jason"
# TODO pass string through text cleaners? 
encoded = sp.EncodeAsIds(s)
assert 0 not in encoded, "tried to encode an unknown character"
print(" ".join(str(idx) for idx in encoded))

1 10 2 12 12 4 1 17 4 9 12 11 1 16 20 1 6 5 16 2 1 7 8 1 26 5 8 4 6


In [380]:
sp.DecodeIds(encoded)

'hello world my name is jason'

# NEW! SIMPLE TOKENIZER

In [381]:
from speechbrain.tokenizers.SimpleTokenizer import SimpleTokenizer

In [382]:
tokenizer = SimpleTokenizer()

In [383]:
text = "hello my name is jason"
text = text.replace(' ', '|')
print(text)
ids = tokenizer.encode_as_ids(text)
ids

hello|my|name|is|jason


[9, 6, 13, 13, 16, 1, 14, 26, 1, 15, 2, 14, 6, 1, 10, 20, 1, 11, 2, 20, 16, 15]

In [384]:
tokenizer.decode_ids(ids)

'hello|my|name|is|jason'

## test simple tokenizer with probability distribution, and see if CTC decoder successfully generates n-best lists

In [385]:
# create empty array of correct dimensions
min_len, max_len = 50, 100
bsz = 4
lens = torch.randint(min_len, max_len, (bsz,))
vocab_size = len(tokenizer.vocab)

# randomly assign probaility distribution to each timestep

# try to decode

In [386]:
randn = torch.randn(bsz, max_len, vocab_size)

In [387]:
ctc_probs = softmax(randn, dim=1)
# ctc_probs

In [388]:
ctc_beamsearch_decoder_test = ctc_decoder(
    lexicon=None,
    # tokens="/home/s1785140/rlspeller/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/tokens.txt",
    tokens=tokenizer.vocab,
    nbest=2,
    blank_token='-',
    sil_token="|",
)

predicted_ids = ctc_beamsearch_decoder_test(ctc_probs, lens)

predicted_words = []
for i, hyps in enumerate(predicted_ids):
    for j, hyp in enumerate(hyps):
        words = tokenizer.decode_ids(hyp.tokens.tolist()).split(" ")
        tup = (f"sample {i+1}, hyp {j+1}/{len(hyps)}", words)
        predicted_words.append(tup)
        print(tup)

('sample 1, hyp 1/2', ['|jshwvbilavjumrpeinyvzvznefekdebiz|shc|viyv|rgeqbzax|aonxq|iayewknbt|bwkoswuo|bxmncoadxydlm|'])
('sample 1, hyp 2/2', ['|jshwvbilavjumrpeinyvzvznefekdebiz|shc|viyv|rgeqbzax|aonxq|iayewknbt|bwkoswuoybxmncoadxydlm|'])
('sample 2, hyp 1/2', ['|omecu|f|ufsgkeglhxwkcnsotflrmjdwqjenpnzsrvlwpxakir|xsvnkmhcoxaidtobunwjpcgqhuityfzlhlizvj|'])
('sample 2, hyp 2/2', ['|omecu|f|ufsgkeglhxwkcnsotflrmjdwqjenpnzsrvlwpxakir|xsvnkmhcoxaidtobunwjpcgqhubtyfzlhlizvj|'])
('sample 3, hyp 1/2', ['|mcabdpfgrstqlczxyxkokni|auarevcd|hrprnljrfvbqzckckwf|xfebos|tctgmsmocnoiofhcg|nteswduywlcxus|'])
('sample 3, hyp 2/2', ['|mcabdpfgrstqlczxyxkokni|auarevcd|hrprnljrfvbqzckckwf|xfebos|tctgmsmocnoiofhcg|bteswduywlcxus|'])
('sample 4, hyp 1/2', ['|tusmtncyfzkvyhjtkubup|gapbtuzltjvosrobeliyxzdlgeoeoivqlybygnlwjxzrc|chxtndimx|uardhszinjypf|'])
('sample 4, hyp 2/2', ['|tusmtncvfzkvyhjtkubup|gapbtuzltjvosrobeliyxzdlgeoeoivqlybygnlwjxzrc|chxtndimx|uardhszinjypf|'])


# LOAD ASR (PRETRAINED)

In [389]:
from templates.speech_recognition_CharTokens_NoLM.ASR.train import ASR
from templates.speech_recognition_CharTokens_NoLM.ASR.train import dataio_prepare
from torch.utils.data import DataLoader
from speechbrain.dataio.dataloader import LoopedLoader

In [390]:
# Load hyperparameters file with command-line overrides
speechbrain_hparams_file = hparams['speechbrain_hparams_file']
with open(speechbrain_hparams_file) as f:
    speechbrain_hparams = hyperpyyaml.load_hyperpyyaml(f)

/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/rirs_noises.zip exists. Skipping download


In [391]:
speechbrain_hparams['save_folder']

'/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/ASR/results/CRDNN_CHAR_LJSpeech_halved_subsampling1x/2602/save'

In [392]:
# initialise trainer (we don't want to train, but model is tightly coupled with trainer)
asr_brain = ASR(
    modules=speechbrain_hparams["modules"],
    opt_class=speechbrain_hparams["opt_class"],
    hparams=speechbrain_hparams,
    checkpointer=speechbrain_hparams["checkpointer"],
)



def setup_asr_brain_for_infer(asr_brain, enable_dropout=False):
    asr_brain.on_evaluate_start(min_key="WER") # We call the on_evaluate_start that will load the best model
    if enable_dropout:
        asr_brain.modules.train()
    else:
        asr_brain.modules.eval() # We set the model to eval mode (remove dropout etc)

print("if on_evaluate_start() get runtime error, likely need to restart notebook kernel")
setup_asr_brain_for_infer(asr_brain, enable_dropout=True)

if on_evaluate_start() get runtime error, likely need to restart notebook kernel


In [393]:
# create dataset and dataloader for inference
datasets = dataio_prepare(speechbrain_hparams)

test_set = datasets['test']

if not isinstance(test_set, DataLoader) or isinstance(test_set, LoopedLoader):
    test_loader_kwargs=speechbrain_hparams["test_dataloader_opts"]
    test_set = asr_brain.make_dataloader(
        test_set, stage=sb.Stage.TEST, **test_loader_kwargs
    )

In [394]:
# get vocab from tokenizer (needed for ctc decoding)
vocab_size = len(asr_brain.hparams.tokenizer)
vocab = []
for i in range(vocab_size):
    vocab.append(asr_brain.hparams.tokenizer.decode_ids([i]))
print(vocab)

# edit vocab to match default ctc decoder symbols for blank and silence
vocab[0] = '-'
vocab[1] = "|"

print(vocab)

[' ⁇ ', '', 'e', 't', 'o', 'a', 'n', 'i', 's', 'r', 'h', 'd', 'l', 'c', 'f', 'u', 'm', 'w', 'p', 'g', 'y', 'b', 'v', 'k', 'x', 'q', 'j', 'z']
['-', '|', 'e', 't', 'o', 'a', 'n', 'i', 's', 'r', 'h', 'd', 'l', 'c', 'f', 'u', 'm', 'w', 'p', 'g', 'y', 'b', 'v', 'k', 'x', 'q', 'j', 'z']


In [395]:
ctc_beamsearch_decoder = ctc_decoder(
    lexicon=None,
    # tokens="/home/s1785140/rlspeller/templates/speech_recognition_CharTokens_NoLM/Tokenizer/save/tokens.txt",
    tokens=vocab,
    nbest=100,
    blank_token='-',
    sil_token="|",
)

In [396]:
# generate transcriptions for all batches in test set
def transcribe_dataset(asr_brain, dataset, greedy=False, num_batches_to_transcribe=None):
    # Now we iterate over the dataset and we simply compute_forward and decode
    with torch.no_grad():
        transcripts = []
        for batch in tqdm(list(dataset)[:num_batches_to_transcribe], dynamic_ncols=True):
            orig_transcriptions = batch.words

            # Make sure that your compute_forward returns the predictions !!!
            # In the case of the template, when stage = TEST, a beam search is applied 
            # in compute_forward(). 
            predictions = asr_brain.compute_forward(batch, stage=sb.Stage.TEST)
            
            ctc_probs = predictions['ctc_logprobs'] # FOR DEBUG

            if greedy:
                predicted_ids = sb.decoders.ctc_greedy_decode(
                    predictions["ctc_logprobs"], asr_brain.feat_lens, blank_id=asr_brain.hparams.blank_index
                )
                predicted_words = [
                    asr_brain.tokenizer.decode_ids(ids).split(" ")
                    for ids in predicted_ids
                ]
            else:
                # get mel lens from wav len ratios since torch ctc decoder requires lens in frames
                batch_max_len = predictions["ctc_logprobs"].size(1)
                bsz = predictions["ctc_logprobs"].size(0)
                mel_lens = torch.zeros(bsz)
                for i, len_ratio in enumerate(asr_brain.feat_lens):
                    mel_lens[i] = int(torch.round(len_ratio * batch_max_len))
                
                predicted_ids = ctc_beamsearch_decoder(
                    predictions["ctc_logprobs"], lengths=mel_lens
                )

                predicted_words = []
                for i, (utt_id, orig_text, hyps) in enumerate(zip(batch.utt_id, orig_transcriptions, predicted_ids)):
                    print(f"\nsample {i+1} - ({utt_id}: '{orig_text}')")
                    sample_cers = []
                    for j, hyp in enumerate(hyps):
                        words = asr_brain.hparams.tokenizer.decode_ids(hyp.tokens.tolist()) # .split("|")
                        # words = tokenizer.decode_ids(hyp.tokens.tolist()) # .split("|")
                        hyp_cer = 100 * cer(orig_text, words)
                        sample_cers.append(hyp_cer)
                        print(f"\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'")
                        predicted_words.append((f"sample {i+1}, hyp {j+1}/{len(hyps)}", words))
                        
                    print(f"\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ===")

            transcripts.append(predicted_words)

    return transcripts, ctc_probs

# transcripts, ctc_probs = transcribe_dataset(asr_brain, test_set, greedy=False, num_batches_to_transcribe=1)

# LOAD WORD ALIGNED WAVS into dataset

In [397]:
# imitate CLAs
import sys
import argparse
import math
import glob
from tqdm import tqdm

In [398]:
# set these in yaml config!
train_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_train_wordtoken_annotation.json'
valid_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_valid_wordtoken_annotation.json'
test_annotation_path = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_test_wordtoken_annotation.json'

In [399]:
speechbrain_hparams['train_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_train_wordtoken_annotation.json'
speechbrain_hparams['valid_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_valid_wordtoken_annotation.json'
speechbrain_hparams['test_annotation'] = '/home/s1785140/speechbrain/templates/speech_recognition_CharTokens_NoLM/data/respeller_test_wordtoken_annotation.json'

In [400]:
def dataio_prepare(hparams):
    """This function prepares the datasets to be used in the brain class.
    It also defines the data processing pipeline through user-defined functions.


    Arguments
    ---------
    hparams : dict
        This dictionary is loaded from the `train.yaml` file, and it includes
        all the hyperparameters needed for dataset construction and loading.

    Returns
    -------
    datasets : dict
        Dictionary containing "train", "valid", and "test" keys that correspond
        to the DynamicItemDataset objects.
    """
    # Define audio pipeline. In this case, we simply read the path contained
    # in the variable wav with the audio reader.
    # wav path like: data/ljspeech_wavs_16khz_word_aligned/differs/differs__LJ001-0001__occ1__len8320.wav
    @sb.utils.data_pipeline.takes("wav")
    @sb.utils.data_pipeline.provides("sig", "wav_path", "utt_id")
    def audio_pipeline(wav_path):
        """Load the audio signal. This is done on the CPU in the `collate_fn`."""
        sig = sb.dataio.dataio.read_audio(wav_path)
        yield sig

        yield wav_path

        utt_id = wav_path.split("/")[-1].split(".")[0]
        yield utt_id

    @sb.utils.data_pipeline.takes("samples_to_graphemes_ratio")
    @sb.utils.data_pipeline.provides("samples_to_graphemes_ratio")
    def ratio_pipeline(samples_to_graphemes_ratio):
        yield samples_to_graphemes_ratio

    @sb.utils.data_pipeline.takes("length")
    @sb.utils.data_pipeline.provides("length")
    def length_pipeline(length):
        yield length

    @sb.utils.data_pipeline.takes("words")
    @sb.utils.data_pipeline.provides("words")
    def text_pipeline(words):
        """Processes the transcriptions to generate proper labels

        NB Make sure that you yield exactly what is defined above in @sb.utils.data_pipeline.provides()"""
        yield words

        # TODO also yield mel for calculating fastpitch softdtw loss

    # Define datasets from json data manifest file
    # Define datasets sorted by ascending lengths for efficiency
    datasets = {}
    data_info = {
        "train": hparams["train_annotation"],
        "valid": hparams["valid_annotation"],
        "test": hparams["test_annotation"],
    }

    for split in data_info:
        datasets[split] = sb.dataio.dataset.DynamicItemDataset.from_json(
            json_path=data_info[split],
            dynamic_items=[audio_pipeline, ratio_pipeline, length_pipeline, text_pipeline],
            output_keys=[
                "id",
                "sig",
                "wav_path",
                "utt_id",
                "samples_to_graphemes_ratio",
                "length",
                "words",
            ],
        )
        hparams[f"{split}_dataloader_opts"]["shuffle"] = True

    def print_dataset_lens(extra_str):
        for split in data_info:
            dataset_split = datasets[split]
            print(f"{split} dataset has {len(dataset_split)} samples", extra_str)

    print_dataset_lens("before any filtering")

    # Filter data for samples_to_graphemes_ratio that is either too small or too large
    key_min_value = {}
    if hparams["min_samples_to_graphemes_ratio"] is not None:
        key_min_value = {"samples_to_graphemes_ratio": hparams["min_samples_to_graphemes_ratio"]}

    key_max_value = {}
    if hparams["max_samples_to_graphemes_ratio"] is not None:
        key_max_value = {"samples_to_graphemes_ratio": hparams["max_samples_to_graphemes_ratio"]}

    for split in data_info:
        datasets[split] = datasets[split].filtered_sorted(
            key_min_value=key_min_value,
            key_max_value=key_max_value,
        )
    print_dataset_lens("after filtering by min and max samples to graphemes ratio")

    # Filter samples whos length is too short
    key_min_value = {}
    if hparams["min_length_seconds"] is not None:
        key_min_value = {"length": hparams["min_length_seconds"]}
    for split in data_info:
        datasets[split] = datasets[split].filtered_sorted(
            key_min_value=key_min_value,
        )
    print_dataset_lens("after filtering by minimum length")

    # Sorting training data with ascending order makes the code  much
    # faster  because we minimize zero-padding. In most of the cases, this
    # does not harm the performance.
    if hparams["sorting"] == "ascending":
        datasets["train"] = datasets["train"].filtered_sorted(sort_key="length")
        hparams["train_dataloader_opts"]["shuffle"] = False

    elif hparams["sorting"] == "descending":
        datasets["train"] = datasets["train"].filtered_sorted(
            sort_key="length", reverse=True
        )
        hparams["train_dataloader_opts"]["shuffle"] = False

    elif hparams["sorting"] == "random":
        hparams["train_dataloader_opts"]["shuffle"] = True
        pass

    else:
        raise NotImplementedError(
            "sorting must be random, ascending or descending"
        )
    
    return datasets

datasets = dataio_prepare(speechbrain_hparams)

train dataset has 11453 samples before any filtering
valid dataset has 415 samples before any filtering
test dataset has 414 samples before any filtering
train dataset has 10642 samples after filtering by min and max samples to graphemes ratio
valid dataset has 391 samples after filtering by min and max samples to graphemes ratio
test dataset has 384 samples after filtering by min and max samples to graphemes ratio
train dataset has 10622 samples after filtering by minimum length
valid dataset has 389 samples after filtering by minimum length
test dataset has 384 samples after filtering by minimum length


In [401]:
# convert from datasets to dataloaders
split2stage = {"train": sb.Stage.TRAIN, "valid": sb.Stage.VALID, "test": sb.Stage.TEST}
for split in ["train", "valid", "test"]:
    if not isinstance(datasets[split], DataLoader) or isinstance(datasets[split], LoopedLoader):
        dataloader_kwargs=speechbrain_hparams[f"{split}_dataloader_opts"]
        datasets[split] = asr_brain.make_dataloader(
            datasets[split], stage=split2stage[split], **dataloader_kwargs
        )

In [402]:
def set_whitespace_to_0_probability(ctc_probs, vocab, log_probs=True, whitespace_symbol="|"):
    """ctc_probs [bsz, max_seq_len, vocab_size]"""
    new_probability = -math.inf if log_probs else 0.0
    ctc_probs[:,:,vocab.index(whitespace_symbol)] = new_probability
    return ctc_probs

# TRANSCRIBE WORD ALIGNED WAVS

In [403]:
from collections import defaultdict

# generate transcriptions for all batches in test set
def transcribe_dataset(asr_brain, dataset, 
                       num_batches_to_transcribe=None,
                       hack_whitespace_probs=False, collapse_whitespace=True,
                       print_info=False, max_hyps_per_sample=None,
                       wordtypes_to_transcribe=[]):
    # Now we iterate over the dataset and we simply compute_forward and decode

    orig_words = []
    printouts = []
    orig_wavs = []
    transcribed_words = defaultdict(list)
    n = 0 # number of batches transcribed

    with torch.no_grad():
        for batch in tqdm(dataset, dynamic_ncols=True, total=num_batches_to_transcribe):
            # break out of loop if we have transcribed enough batches
            if n >= num_batches_to_transcribe:
                break
            n += 1

            orig_transcriptions = batch.words
            wavs = batch.sig.data

            # Make sure that your compute_forward returns the predictions !!!
            # In the case of the template, when stage = TEST, a beam search is applied 
            # in compute_forward(). 
            predictions = asr_brain.compute_forward(batch, stage=sb.Stage.TEST)
            ctc_probs = predictions['ctc_logprobs'] # FOR DEBUG

            # hack probabilities to set all probs to 0 for whitespace
            if hack_whitespace_probs:
                ctc_probs = set_whitespace_to_0_probability(ctc_probs, vocab, log_probs=True, whitespace_symbol="|")

            # get mel lens from wav len ratios since torch ctc decoder requires lens in frames
            batch_max_len = predictions["ctc_logprobs"].size(1)
            bsz = predictions["ctc_logprobs"].size(0)
            mel_lens = torch.zeros(bsz)
            for i, len_ratio in enumerate(asr_brain.feat_lens):
                mel_lens[i] = int(torch.round(len_ratio * batch_max_len))
            
            predicted_ids = ctc_beamsearch_decoder(
                predictions["ctc_logprobs"], lengths=mel_lens
            )

            # iterate over samples in batch
            for i, (utt_id, orig_text, hyps, wav) in enumerate(zip(batch.utt_id, orig_transcriptions, predicted_ids, wavs)):
                sample_printout = f"\nsample {i+1} - ({utt_id}: '{orig_text}')"
                orig_utt_text = "INSERT ORIG UTT TEXT"
                sample_printout += f"\nOriginal Utterance: {orig_utt_text}"
                # if print_info: print(f"\nsample {i+1} - ({utt_id}: '{orig_text}')")
                sample_cers = []
                for j, hyp in enumerate(list(hyps)[:max_hyps_per_sample]):
                    words = asr_brain.hparams.tokenizer.decode_ids(hyp.tokens.tolist())
                    if collapse_whitespace:
                        words = "".join(c for c in words if c != " ")
                    hyp_cer = 100 * cer(orig_text, words)
                    sample_cers.append(hyp_cer)
                    sample_printout += f"\n\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'"
                    # if print_info: print(f"\thyp {j+1}/{len(hyps)} (CER={hyp_cer:.1f}%): '{words}'")
                    if not wordtypes_to_transcribe or orig_text in wordtypes_to_transcribe:
                        transcribed_words[orig_text].append(words)
                    
                sample_printout += f"\n\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ==="
                # if print_info: print(f"\t=== Mean CER: {np.mean(sample_cers):.1f}%, Std CER: {np.std(sample_cers):.1f}% ===")

                if not wordtypes_to_transcribe or orig_text in wordtypes_to_transcribe:
                    orig_words.append(orig_text)
                    printouts.append(sample_printout)
                    orig_wavs.append(wav)

    output_dict = {
        "orig_words": orig_words,
        "transcribed_words": transcribed_words,
        "wavs": orig_wavs,
        "printouts": printouts,
    }

    return output_dict


## Compare hack with no hack (to set prob of whitespace to 0)

In [404]:
# NUM_BATCHES_TO_TRANSCRIBE = 1
# MAX_HYPS_PER_SAMPLE = 20

# transcription_output_dict_no_hack = transcribe_dataset(asr_brain, datasets["train"], 
#                                                num_batches_to_transcribe=NUM_BATCHES_TO_TRANSCRIBE,
#                                                collapse_whitespace=False,
#                                                max_hyps_per_sample=MAX_HYPS_PER_SAMPLE)

# transcription_output_dict_hack = transcribe_dataset(asr_brain, datasets["train"], 
#                                                num_batches_to_transcribe=NUM_BATCHES_TO_TRANSCRIBE,
#                                                collapse_whitespace=False, hack_whitespace_probs=True,
#                                                max_hyps_per_sample=MAX_HYPS_PER_SAMPLE)

# for printout1, printout2, wav in zip(transcription_output_dict_no_hack["printouts"], 
#                          transcription_output_dict_hack["printouts"], 
#                          transcription_output_dict_no_hack["wavs"]):
#     print('NO HACK', printout1)
#     print('HACK', printout2)
#     display(Audio(wav, rate=16000))

100%|███████████████████████████████████████████████████████| 1/1 [00:02<00:00,  2.40s/it]

NO HACK 
sample 1 - (unconstitutionality__LJ021-0191__occ1__len25760: 'unconstitutionality')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=10.5%): 'on constitutionality '
	hyp 2/50 (CER=5.3%): 'un constitutionality '
	hyp 3/50 (CER=15.8%): 'on constitution ality '
	hyp 4/50 (CER=10.5%): 'un constitution ality '
	hyp 5/50 (CER=15.8%): 'on constitutionaloity '
	hyp 6/50 (CER=15.8%): 'on constitu tionality '
	hyp 7/50 (CER=15.8%): 'on constitutionaloty '
	hyp 8/50 (CER=10.5%): 'un constitutionaloity '
	hyp 9/50 (CER=21.1%): 'on constitution aloity '
	hyp 10/50 (CER=10.5%): 'un constitu tionality '
	hyp 11/50 (CER=10.5%): 'un constitutionaloty '
	hyp 12/50 (CER=21.1%): 'on constitu tion ality '
	hyp 13/50 (CER=21.1%): 'on constitution aloty '
	hyp 14/50 (CER=15.8%): 'un constitution aloity '
	hyp 15/50 (CER=15.8%): 'un constitu tion ality '
	hyp 16/50 (CER=15.8%): 'un constitution aloty '
	hyp 17/50 (CER=10.5%): 'oun constitutionality '
	hyp 18/50 (CER=15.8%): 'on constituti onal

NO HACK 
sample 2 - (anesthesiologists__LJ031-0023__occ1__len24000: 'anesthesiologists')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=52.9%): 'an as thease eolgiests '
	hyp 2/50 (CER=47.1%): 'an as thease eolgists '
	hyp 3/50 (CER=58.8%): 'an as thease eolgiest s '
	hyp 4/50 (CER=52.9%): 'an as thease eolgests '
	hyp 5/50 (CER=58.8%): 'an as thease e olgiests '
	hyp 6/50 (CER=52.9%): 'an as thease eolgist s '
	hyp 7/50 (CER=58.8%): 'an as thease eolgest s '
	hyp 8/50 (CER=52.9%): 'an as thease e olgists '
	hyp 9/50 (CER=64.7%): 'an as thease e olgiest s '
	hyp 10/50 (CER=47.1%): 'an as theaseeolgiests '
	hyp 11/50 (CER=58.8%): 'an as thease e olgests '
	hyp 12/50 (CER=58.8%): 'and as thease eolgiests '
	hyp 13/50 (CER=47.1%): 'anas thease eolgiests '
	hyp 14/50 (CER=58.8%): 'an as thease e olgist s '
	hyp 15/50 (CER=41.2%): 'an as theaseeolgists '
	hyp 16/50 (CER=52.9%): 'an as theaseeolgiest s '
	hyp 17/50 (CER=64.7%): 'an as thease e olgest s '
	hyp 18/50 (CER=52.9%): 'and

NO HACK 
sample 3 - (misrepresentations__LJ005-0034__occ1__len23200: 'misrepresentations')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=11.1%): 'misrepras entations '
	hyp 2/50 (CER=16.7%): 'mis repras entations '
	hyp 3/50 (CER=11.1%): 'misreprs entations '
	hyp 4/50 (CER=16.7%): 'misreprase entations '
	hyp 5/50 (CER=16.7%): 'misrepras untations '
	hyp 6/50 (CER=16.7%): 'misrebras entations '
	hyp 7/50 (CER=16.7%): 'mis reprs entations '
	hyp 8/50 (CER=22.2%): 'mis reprase entations '
	hyp 9/50 (CER=16.7%): 'misrebpras entations '
	hyp 10/50 (CER=22.2%): 'mis repras untations '
	hyp 11/50 (CER=22.2%): 'mis rebras entations '
	hyp 12/50 (CER=16.7%): 'missrepras entations '
	hyp 13/50 (CER=22.2%): 'mis rebpras entations '
	hyp 14/50 (CER=11.1%): 'misreprse entations '
	hyp 15/50 (CER=16.7%): 'misreprs untations '
	hyp 16/50 (CER=22.2%): 'miss repras entations '
	hyp 17/50 (CER=16.7%): 'misrebrs entations '
	hyp 18/50 (CER=11.1%): 'misrepris entations '
	hyp 19/50 (CER=16.7%)

NO HACK 
sample 4 - (institutionalized__LJ040-0144__occ1__len21760: 'institutionalized')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/44 (CER=0.0%): 'institutionalized '
	hyp 2/44 (CER=5.9%): 'institutionalizsed '
	hyp 3/44 (CER=5.9%): 'nstitutionalized '
	hyp 4/44 (CER=11.8%): 'a institutionalized '
	hyp 5/44 (CER=5.9%): 'institutionaliezed '
	hyp 6/44 (CER=5.9%): 'institutionalinzed '
	hyp 7/44 (CER=5.9%): 'institutionallized '
	hyp 8/44 (CER=11.8%): 'e institutionalized '
	hyp 9/44 (CER=11.8%): 'nstitutionalizsed '
	hyp 10/44 (CER=17.6%): 'a institutionalizsed '
	hyp 11/44 (CER=5.9%): 'institutionalised '
	hyp 12/44 (CER=11.8%): 'a nstitutionalized '
	hyp 13/44 (CER=11.8%): 'institutionaliezsed '
	hyp 14/44 (CER=11.8%): 'nstitutionaliezed '
	hyp 15/44 (CER=17.6%): 'a institutionaliezed '
	hyp 16/44 (CER=0.0%): 'institutionalized '
	hyp 17/44 (CER=0.0%): 'institutionalized '
	hyp 18/44 (CER=11.8%): 'institutionalinzsed '
	hyp 19/44 (CER=11.8%): 'nstitutionalinzed '
	hyp 20/44 (CER

NO HACK 
sample 5 - (specifications__LJ043-0092__occ1__len21600: 'specifications')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/47 (CER=0.0%): 'specifications '
	hyp 2/47 (CER=7.1%): 'spescifications '
	hyp 3/47 (CER=0.0%): 'specifications '
	hyp 4/47 (CER=7.1%): 'specificcations '
	hyp 5/47 (CER=7.1%): 'speecifications '
	hyp 6/47 (CER=7.1%): 'specificationsd '
	hyp 7/47 (CER=7.1%): 'spectifications '
	hyp 8/47 (CER=7.1%): 'spefcifications '
	hyp 9/47 (CER=7.1%): 'spe cifications '
	hyp 10/47 (CER=7.1%): 'specifocations '
	hyp 11/47 (CER=7.1%): 'speciffications '
	hyp 12/47 (CER=7.1%): 'pecifications '
	hyp 13/47 (CER=7.1%): 'speccifications '
	hyp 14/47 (CER=7.1%): 'spetcifications '
	hyp 15/47 (CER=7.1%): 'specificationes '
	hyp 16/47 (CER=7.1%): 'supecifications '
	hyp 17/47 (CER=7.1%): 'spescifications '
	hyp 18/47 (CER=7.1%): 'specificatsions '
	hyp 19/47 (CER=14.3%): 'spescificcations '
	hyp 20/47 (CER=7.1%): 'specsifications '
	=== Mean CER: 6.8%, Std CER: 2.7% ===
HACK 
sam

## Generate multiple times to see if outputs change (i.e. should change if dropout is enabled in model)

In [427]:
NUM_BATCHES_TO_TRANSCRIBE = 5
MAX_HYPS_PER_SAMPLE = 20

wordtypes_to_transcribe = None
# wordtypes_to_transcribe = ['anesthesiologists'] # used for debugging and checking results only for a subset of wordtypes

NUM_ITERATIONS = 5

word_sets = defaultdict(set)

for _ in range(NUM_ITERATIONS):
    transcription_output_dict_hack = transcribe_dataset(asr_brain, datasets["train"], 
                                                num_batches_to_transcribe=NUM_BATCHES_TO_TRANSCRIBE,
                                                collapse_whitespace=False, hack_whitespace_probs=True,
                                                max_hyps_per_sample=MAX_HYPS_PER_SAMPLE,
                                                wordtypes_to_transcribe=wordtypes_to_transcribe)

    for orig_word, printout, wav in zip(transcription_output_dict_hack["orig_words"], transcription_output_dict_hack["printouts"], 
                            transcription_output_dict_hack["wavs"]):
        print(printout)
        display(Audio(wav, rate=16000))

        old_count = len(word_sets[orig_word])
        word_sets[orig_word].update(transcription_output_dict_hack["transcribed_words"][orig_word])
        new_count = len(word_sets[orig_word])
        if new_count > old_count:
            print(f"added {new_count - old_count} new spellings for '{orig_word}' to its word set")

100%|███████████████████████████████████████████████████████| 5/5 [00:10<00:00,  2.06s/it]


sample 1 - (unconstitutionality__LJ021-0191__occ1__len25760: 'unconstitutionality')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=0.0%): 'unconstitutionality '
	hyp 2/50 (CER=5.3%): 'unconstitutionalioty '
	hyp 3/50 (CER=5.3%): 'unconstitutionaloty '
	hyp 4/50 (CER=5.3%): 'unconstitutionaloity '
	hyp 5/50 (CER=5.3%): 'unconstitutionaleity '
	hyp 6/50 (CER=10.5%): 'unconstitutionaleoty '
	hyp 7/50 (CER=5.3%): 'onconstitutionality '
	hyp 8/50 (CER=5.3%): 'unconstitutionalty '
	hyp 9/50 (CER=10.5%): 'onconstitutionalioty '
	hyp 10/50 (CER=10.5%): 'onconstitutionaloty '
	hyp 11/50 (CER=5.3%): 'unconstitutioonality '
	hyp 12/50 (CER=5.3%): 'cunconstitutionality '
	hyp 13/50 (CER=10.5%): 'unconstitutioonalioty '
	hyp 14/50 (CER=10.5%): 'cunconstitutionalioty '
	hyp 15/50 (CER=10.5%): 'onconstitutionaloity '
	hyp 16/50 (CER=5.3%): 'unconstitutsionality '
	hyp 17/50 (CER=10.5%): 'unconstitutioonaloty '
	hyp 18/50 (CER=10.5%): 'cunconstitutionaloty '
	hyp 19/50 (CER=5.3%): 'unconstit

added 20 new spellings for 'unconstitutionality' to its word set

sample 2 - (anesthesiologists__LJ031-0023__occ1__len24000: 'anesthesiologists')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=23.5%): 'anastheaseologests '
	hyp 2/50 (CER=29.4%): 'anastheaseeologests '
	hyp 3/50 (CER=29.4%): 'anastheaseollogests '
	hyp 4/50 (CER=35.3%): 'anastheaseeollogests '
	hyp 5/50 (CER=17.6%): 'anastheseologests '
	hyp 6/50 (CER=23.5%): 'anastheseeologests '
	hyp 7/50 (CER=23.5%): 'anastheseollogests '
	hyp 8/50 (CER=29.4%): 'andastheaseologests '
	hyp 9/50 (CER=29.4%): 'anastheseeollogests '
	hyp 10/50 (CER=35.3%): 'andastheaseeologests '
	hyp 11/50 (CER=29.4%): 'anastheasheologests '
	hyp 12/50 (CER=35.3%): 'anastheaseheologests '
	hyp 13/50 (CER=35.3%): 'andastheaseollogests '
	hyp 14/50 (CER=23.5%): 'anistheaseologests '
	hyp 15/50 (CER=41.2%): 'andastheaseeollogests '
	hyp 16/50 (CER=35.3%): 'anastheasheollogests '
	hyp 17/50 (CER=29.4%): 'anastheaseologest '
	hyp 18/50 (CER=29.4%): 

added 20 new spellings for 'anesthesiologists' to its word set

sample 3 - (misrepresentations__LJ005-0034__occ1__len23200: 'misrepresentations')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/45 (CER=5.6%): 'misreprsentations '
	hyp 2/45 (CER=11.1%): 'misreprsuntations '
	hyp 3/45 (CER=11.1%): 'missreprsentations '
	hyp 4/45 (CER=11.1%): 'misrepersentations '
	hyp 5/45 (CER=11.1%): 'misreprsontations '
	hyp 6/45 (CER=5.6%): 'misreprasentations '
	hyp 7/45 (CER=16.7%): 'missreprsuntations '
	hyp 8/45 (CER=11.1%): 'misreprseentations '
	hyp 9/45 (CER=16.7%): 'misrepersuntations '
	hyp 10/45 (CER=16.7%): 'missrepersentations '
	hyp 11/45 (CER=11.1%): 'misreprsemntations '
	hyp 12/45 (CER=11.1%): 'mitsreprsentations '
	hyp 13/45 (CER=16.7%): 'missreprsontations '
	hyp 14/45 (CER=11.1%): 'misreprasuntations '
	hyp 15/45 (CER=11.1%): 'missreprasentations '
	hyp 16/45 (CER=11.1%): 'misreprseuntations '
	hyp 17/45 (CER=11.1%): 'misreporsentations '
	hyp 18/45 (CER=16.7%): 'missreprseentation

added 20 new spellings for 'misrepresentations' to its word set

sample 4 - (institutionalized__LJ040-0144__occ1__len21760: 'institutionalized')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/45 (CER=0.0%): 'institutionalized '
	hyp 2/45 (CER=5.9%): 'institutionaliezed '
	hyp 3/45 (CER=5.9%): 'institutionaliszed '
	hyp 4/45 (CER=5.9%): 'tinstitutionalized '
	hyp 5/45 (CER=5.9%): 'einstitutionalized '
	hyp 6/45 (CER=5.9%): 'institutionaliczed '
	hyp 7/45 (CER=5.9%): 'hinstitutionalized '
	hyp 8/45 (CER=11.8%): 'institutionalieszed '
	hyp 9/45 (CER=5.9%): 'institutionalizsed '
	hyp 10/45 (CER=5.9%): 'institutionalizced '
	hyp 11/45 (CER=11.8%): 'tinstitutionaliezed '
	hyp 12/45 (CER=11.8%): 'einstitutionaliezed '
	hyp 13/45 (CER=5.9%): 'nstitutionalized '
	hyp 14/45 (CER=5.9%): 'institutionallized '
	hyp 15/45 (CER=11.8%): 'institutionalieczed '
	hyp 16/45 (CER=5.9%): 'institutionalimzed '
	hyp 17/45 (CER=5.9%): 'institutionalinzed '
	hyp 18/45 (CER=11.8%): 'tinstitutionaliszed '
	hyp 1

...

added 6 new spellings for 'insensibility' to its word set

sample 2 - (humanitarianism__LJ016-0382__occ1__len20000: 'humanitarianism')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=26.7%): 'shemaniterinism '
	hyp 2/50 (CER=26.7%): 'shemaniteriunism '
	hyp 3/50 (CER=20.0%): 'shumaniterinism '
	hyp 4/50 (CER=20.0%): 'shumaniteriunism '
	hyp 5/50 (CER=26.7%): 'sheumaniterinism '
	hyp 6/50 (CER=26.7%): 'sheumaniteriunism '
	hyp 7/50 (CER=20.0%): 'hemaniterinism '
	hyp 8/50 (CER=20.0%): 'hemaniteriunism '
	hyp 9/50 (CER=13.3%): 'humaniterinism '
	hyp 10/50 (CER=13.3%): 'humaniteriunism '
	hyp 11/50 (CER=26.7%): 'shemaniterionism '
	hyp 12/50 (CER=33.3%): 'shemaniteriounism '
	hyp 13/50 (CER=20.0%): 'shumaniterionism '
	hyp 14/50 (CER=26.7%): 'shumaniteriounism '
	hyp 15/50 (CER=20.0%): 'heumaniterinism '
	hyp 16/50 (CER=20.0%): 'heumaniteriunism '
	hyp 17/50 (CER=26.7%): 'sheumaniterionism '
	hyp 18/50 (CER=33.3%): 'sheumaniteriounism '
	hyp 19/50 (CER=26.7%): 'fhemaniterinism '
	


sample 3 - (photosynthesis__LJ026-0161__occ1__len19840: 'photosynthesis')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=42.9%): 'photofsinpises '
	hyp 2/50 (CER=50.0%): 'photofsimnpises '
	hyp 3/50 (CER=42.9%): 'photofsinfises '
	hyp 4/50 (CER=50.0%): 'photofsimnfises '
	hyp 5/50 (CER=50.0%): 'photorfsinpises '
	hyp 6/50 (CER=57.1%): 'photorfsimnpises '
	hyp 7/50 (CER=35.7%): 'photofsinphises '
	hyp 8/50 (CER=42.9%): 'photofsinpases '
	hyp 9/50 (CER=42.9%): 'photofsimnphises '
	hyp 10/50 (CER=50.0%): 'photofsimnpases '
	hyp 11/50 (CER=35.7%): 'photofsintises '
	hyp 12/50 (CER=42.9%): 'photofsimntises '
	hyp 13/50 (CER=50.0%): 'photorfsinfises '
	hyp 14/50 (CER=57.1%): 'photorfsimnfises '
	hyp 15/50 (CER=35.7%): 'photofsinfhises '
	hyp 16/50 (CER=42.9%): 'photofsinfases '
	hyp 17/50 (CER=42.9%): 'photofsimnfhises '
	hyp 18/50 (CER=50.0%): 'photofsimnfases '
	hyp 19/50 (CER=42.9%): 'photorfsinphises '
	hyp 20/50 (CER=42.9%): 'photofsindpises '
	=== Mean CER: 45.4%, Std CER: 6.

added 16 new spellings for 'photosynthesis' to its word set

sample 4 - (anticipations__LJ008-0177__occ1__len19840: 'anticipations')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/45 (CER=23.1%): 'andtisupations '
	hyp 2/45 (CER=30.8%): 'andtosupations '
	hyp 3/45 (CER=30.8%): 'andtisupatiens '
	hyp 4/45 (CER=38.5%): 'andtosupatiens '
	hyp 5/45 (CER=23.1%): 'andticsupations '
	hyp 6/45 (CER=30.8%): 'andtocsupations '
	hyp 7/45 (CER=30.8%): 'andticsupatiens '
	hyp 8/45 (CER=15.4%): 'andticupations '
	hyp 9/45 (CER=30.8%): 'andtesupations '
	hyp 10/45 (CER=38.5%): 'andtocsupatiens '
	hyp 11/45 (CER=23.1%): 'andtocupations '
	hyp 12/45 (CER=23.1%): 'andticupatiens '
	hyp 13/45 (CER=38.5%): 'andtesupatiens '
	hyp 14/45 (CER=30.8%): 'andtocupatiens '
	hyp 15/45 (CER=30.8%): 'andtecsupations '
	hyp 16/45 (CER=38.5%): 'andtecsupatiens '
	hyp 17/45 (CER=23.1%): 'andtecupations '
	hyp 18/45 (CER=30.8%): 'andtecupatiens '
	hyp 19/45 (CER=30.8%): 'andtisupatioens '
	hyp 20/45 (CER=38.5%): 'andto

added 3 new spellings for 'anticipations' to its word set

sample 5 - (uncompromising__LJ001-0068__occ1__len19840: 'uncompromising')
Original Utterance: INSERT ORIG UTT TEXT
	hyp 1/50 (CER=21.4%): 'oncompermising '
	hyp 2/50 (CER=14.3%): 'uncompermising '
	hyp 3/50 (CER=14.3%): 'oncomperomising '
	hyp 4/50 (CER=7.1%): 'uncomperomising '
	hyp 5/50 (CER=21.4%): 'oncompervmising '
	hyp 6/50 (CER=21.4%): 'oncompeormising '
	hyp 7/50 (CER=21.4%): 'oncomperbmising '
	hyp 8/50 (CER=21.4%): 'oncompormising '
	hyp 9/50 (CER=14.3%): 'oncomprmising '
	hyp 10/50 (CER=14.3%): 'uncompervmising '
	hyp 11/50 (CER=14.3%): 'uncompeormising '
	hyp 12/50 (CER=14.3%): 'uncomperbmising '
	hyp 13/50 (CER=14.3%): 'uncompormising '
	hyp 14/50 (CER=7.1%): 'uncomprmising '
	hyp 15/50 (CER=21.4%): 'oncomperlmising '
	hyp 16/50 (CER=28.6%): 'oncomperising '
	hyp 17/50 (CER=21.4%): 'oncomperovmising '
	hyp 18/50 (CER=28.6%): 'oncomepermising '
	hyp 19/50 (CER=21.4%): 'oncomperwmising '
	hyp 20/50 (CER=14.3%): 'onco

added 11 new spellings for 'uncompromising' to its word set


In [428]:
for orig_word, word_set in word_sets.items():
    print(f"\nGenerated {len(word_set)} respellings for '{orig_word}' (ordered a-z):")
    for word in sorted(word_set):
        print(f"\t{word}: {100*cer(orig_word, word):.2f}% CER")


Generated 53 respellings for 'unconstitutionality' (ordered a-z):
	bunconstitutionality : 5.26% CER
	conconstitutionality : 10.53% CER
	cunconstitutionalioty : 10.53% CER
	cunconstitutionality : 5.26% CER
	cunconstitutionaloty : 10.53% CER
	enconstitutionality : 5.26% CER
	gunconstitutionality : 5.26% CER
	hunconstitutionality : 5.26% CER
	nconstitutionality : 5.26% CER
	nonconstitutionality : 10.53% CER
	nunconstitutionality : 5.26% CER
	onconstatutionality : 10.53% CER
	onconstitutionaleity : 10.53% CER
	onconstitutionalioty : 10.53% CER
	onconstitutionality : 5.26% CER
	onconstitutionaloity : 10.53% CER
	onconstitutionaloty : 10.53% CER
	onconstitutionalty : 10.53% CER
	ounconstitutionality : 5.26% CER
	sunconstitutionality : 5.26% CER
	tunconstitutionality : 5.26% CER
	tunconstitutionaloty : 10.53% CER
	unconstatutionalioty : 10.53% CER
	unconstatutionality : 5.26% CER
	unconstatutionaloity : 10.53% CER
	unconstatutionaloty : 10.53% CER
	unconstatutionalty : 10.53% CER
	unconstetu